In [1]:
%pwd

'c:\\Users\\PC\\Desktop\\medical chatbot\\MEDICAL-CHATBOT-\\research'

In [2]:
import os
os.chdir("../")

In [3]:
%pwd

'c:\\Users\\PC\\Desktop\\medical chatbot\\MEDICAL-CHATBOT-'

In [5]:
from langchain.document_loaders import PyPDFLoader,DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [6]:
def load_pdf_files(data):
    loader = DirectoryLoader(data, glob="**/*.pdf", loader_cls=PyPDFLoader)
    documents = loader.load()
    return documents

In [7]:
%pwd

'c:\\Users\\PC\\Desktop\\medical chatbot\\MEDICAL-CHATBOT-'

In [8]:
extracted_data=load_pdf_files("data")

In [9]:
extracted_data

[Document(metadata={'producer': 'PDFlib+PDI 5.0.0 (SunOS)', 'creator': 'PyPDF', 'creationdate': '2004-12-28T15:38:25-05:00', 'moddate': '2005-05-04T13:53:15-06:00', 'author': 'Clifford', 'enhanced': 'By PDF Enhancer 2.5/Win', 'spdf': '1096', 'source': 'data\\medical book.pdf', 'total_pages': 599, 'page': 0, 'page_label': '1'}, page_content='The GALE\nENCYCLOPEDIA of\nAlTERNATIVE\nMEDICINE\nSECOND EDITION\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 1'),
 Document(metadata={'producer': 'PDFlib+PDI 5.0.0 (SunOS)', 'creator': 'PyPDF', 'creationdate': '2004-12-28T15:38:25-05:00', 'moddate': '2005-05-04T13:53:15-06:00', 'author': 'Clifford', 'enhanced': 'By PDF Enhancer 2.5/Win', 'spdf': '1096', 'source': 'data\\medical book.pdf', 'total_pages': 599, 'page': 1, 'page_label': '2'}, page_content='The GALE\nENCYCLOPEDIA of\nAlternative\nMEDICINE\nSECOND EDITION\nJACQUELINE L. LONGE, PROJECT EDITOR\nVOLUME\nD-K\n2\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 3'),
 Document(metadata={'producer': 'PDFlib+P

In [10]:
from typing import List
from langchain.schema import Document
def filter_to_minimal_docs(docs:List[Document]) -> List[Document]:
    """Given a list of Document objects, return a new list of Documnent objects containing only'source' in metadata and the original page_content."""
    minimal_docs = []
    for doc in docs:
        src=doc.metadata.get("source")
        minimal_doc = Document(page_content=doc.page_content, metadata={"source": src})
        minimal_docs.append(minimal_doc)
    return minimal_docs

In [11]:
minimal_docs=filter_to_minimal_docs(extracted_data)

In [12]:
minimal_docs

[Document(metadata={'source': 'data\\medical book.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nAlTERNATIVE\nMEDICINE\nSECOND EDITION\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 1'),
 Document(metadata={'source': 'data\\medical book.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nAlternative\nMEDICINE\nSECOND EDITION\nJACQUELINE L. LONGE, PROJECT EDITOR\nVOLUME\nD-K\n2\nGEAMv2htp/tp  10/11/04  10:45 AM  Page 3'),
 Document(metadata={'source': 'data\\medical book.pdf'}, page_content="The Gale Encyclopedia of Alternative Medicine, Second Edition\nProject Editor\nJacqueline L. Longe\nEditorial\nDeirdre S. Blanchfield, Laurie Fundukian, Erin\nWatts\nEditorial Support Services\nAndrea Lopeman\nRights Acquisition Management\nMargaret Abendroth, Ann T aylor\nImaging\nRandy Bassett, Lezlie Light, Dan W. Newell,\nRobyn V . Y oung\nProduct Design\nMichelle DiMercurio, T racey Rowens\nComposition and Electronic Prepress\nEvi Seoud, Mary Beth T rimper\nManufacturing\nWendy Blurton, Dorothy Maki\nInd

In [13]:
def text_split(minimal_docs):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=500,
        chunk_overlap=20,
        length_function=len,
    )
    texts = text_splitter.split_documents(minimal_docs)
    return texts

In [14]:
texts=text_split(minimal_docs)
print(f"Number of chunks: {len(texts)}")

Number of chunks: 5699


In [19]:
from langchain.embeddings import HuggingFaceEmbeddings
def download_embeddings():
    """Download and return the huggingface embedding models"""
    model_name = "sentence-transformers/all-MiniLM-L6-v2"
    embeddings = HuggingFaceEmbeddings(
        model_name=model_name,
    )
    return embeddings
embedding = download_embeddings()

In [20]:
embedding

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={}, encode_kwargs={}, multi_process=False, show_progress=False)

In [21]:
vector=embedding.embed_query("Hello World")
vector

[-0.03447727486491203,
 0.03102312609553337,
 0.006734980270266533,
 0.026108933612704277,
 -0.03936205804347992,
 -0.16030246019363403,
 0.06692394614219666,
 -0.006441438104957342,
 -0.047450482845306396,
 0.014758863486349583,
 0.07087534666061401,
 0.05552757531404495,
 0.019193356856703758,
 -0.02625126577913761,
 -0.01010954286903143,
 -0.026940442621707916,
 0.022307462990283966,
 -0.02222665585577488,
 -0.14969263970851898,
 -0.017493024468421936,
 0.007676282897591591,
 0.054352231323719025,
 0.0032544038258492947,
 0.03172588348388672,
 -0.08462139964103699,
 -0.029405992478132248,
 0.051595550030469894,
 0.048124078661203384,
 -0.003314835485070944,
 -0.05827915295958519,
 0.04196925833821297,
 0.022210702300071716,
 0.1281888633966446,
 -0.022338951006531715,
 -0.011656239628791809,
 0.06292837113142014,
 -0.03287634998559952,
 -0.09122604131698608,
 -0.03117534890770912,
 0.052699536085128784,
 0.04703483358025551,
 -0.08420310169458389,
 -0.030056182295084,
 -0.0207448396

In [22]:
from dotenv import load_dotenv
import os
load_dotenv()

True

In [23]:
PINECONE_API_KEY=os.getenv("PINECONE_API_KEY")
OPENAI_API_KEY=os.getenv("OPENAI_API_KEY")


os.environ["PINECONE_API_KEY"]=PINECONE_API_KEY
os.environ["OPENAI_API_KEY"]=OPENAI_API_KEY

In [24]:
from pinecone import Pinecone
pinecone_api_key=PINECONE_API_KEY

pc=Pinecone(api_key=pinecone_api_key)

In [25]:
pc

In [29]:
from pinecone import Pinecone, ServerlessSpec


In [30]:
pc = Pinecone(api_key=PINECONE_API_KEY)


In [35]:
if not pc.has_index(index_name):
    pc.create_index(
        name=index_name,
        dimension=384,
        metric="cosine",
        spec=ServerlessSpec(cloud="aws", region="us-east-1")
    )
index = pc.Index(index_name)


In [36]:
from langchain_pinecone import PineconeVectorStore
docsearch=PineconeVectorStore.from_documents(
    documents=texts,
    embedding=embedding,
    index_name=index_name 
)

In [ ]:
#add more data to the exisitng pinecone index

In [38]:
dswith=Document(
    page_content="New medical research data on heart disease.",
    metadata={"source": "data/heart_disease_research.pdf"}
)

In [39]:
docsearch.add_documents(documents=[dswith])

['7da45fc1-1bc4-46b4-b57d-855b48ea73f4']

In [40]:
retriever=docsearch.as_retriever(search_type="similarity", search_kwargs={"k":3})

In [42]:
retrieved_docs=retriever.invoke("What is Acne?")
retrieved_docs

[Document(id='c87769be-85eb-4adc-9ec5-c0ca2763c288', metadata={'source': 'data\\medical book.pdf'}, page_content='A\nAbscess\nAcidophilus\nAcne\nAconite\nAcupressure\nAcupuncture\nAdemetionine\nAdie’s pupil\nAfrican pygeum\nAgastache\nAging\nAIDS\nAlcoholism\nAlexander technique\nAlfalfa\nAlisma\nAllergies\nAllium cepa\nAloe\nAlpha-hydroxy\nAlzheimer’s disease\nAmino acids\nAndrographis\nAndrostenedione\nAnemarrhena\nAnemia\nAngelica root\nAngina\nAnise\nAnkylosing spondylitis\nAnorexia nervosa\nAnthroposophical medicine\nAntioxidants\nAnxiety\nBates method\nBayberry\nBedsores\nBedwetting\nBee pollen\nBehavioral optometry\nBehavioral therapy'),
 Document(id='17ec58de-2acf-42bb-86d5-953cba563cce', metadata={'source': 'data\\medical book.pdf'}, page_content='Atopy —A group of diseases, including eczema,\nthat develop in people with an inherited tendency\nto develop immediate antibodies to common en-\nvironmental allergens.\nCorticosteroids —A group of synthetic hormones\nthat are used to

In [43]:
from langchain_openai import ChatOpenAI
chatModel = ChatOpenAI(model_name="gpt-4o", temperature=0)

In [44]:

from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

In [45]:
system_prompt = (
    "You are an Medical assistant for question-answering tasks. "
    "Use the following pieces of retrieved context to answer "
    "the question. If you don't know the answer, say that you "
    "don't know. Use three sentences maximum and keep the "
    "answer concise."
    "\n\n"
    "{context}"
)


prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_prompt),
        ("human", "{input}"),
    ]
)

In [46]:
question_answer_chain=create_stuff_documents_chain(chatModel,prompt)
rag_chain=create_retrieval_chain(retriever,question_answer_chain)

In [48]:
response = rag_chain.invoke({"input": "what is Acromegaly and gigantism?"})
print(response["answer"])

RateLimitError: Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}